# Test on Velodyne data

In [1]:
%matplotlib widget
import numpy as np
import os
import time
import plotly.graph_objects as go

from planeslam.general import downsample, adaptive_downsample
from planeslam.mesh import LidarMesh
from planeslam.scan import Scan
from planeslam.clustering import cluster_mesh_graph_search, plot_clusters
from planeslam.extraction import scan_from_clusters, planes_from_clusters
from planeslam.general import pc_plot_trace
from planeslam.geometry.util import quat_to_R

%load_ext autoreload
%autoreload 2

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


Flight room

In [18]:
# Read in data
frame_num = 200

pcpath = os.path.join(os.getcwd(),'..', '..', 'data', 'velodyne', '8_12_2022', 'flightroom', 'run_1', 'pcs')
filename = pcpath + '/pc_' + str(frame_num) + '.npy'
PC = np.load(filename)

posepath = os.path.join(os.getcwd(),'..', '..', 'data', 'velodyne', '8_12_2022', 'flightroom', 'run_1', 'poses')
filename = posepath + '/pose_' + str(frame_num) + '.npy'
pose = np.load(filename)

In [19]:
PC = (quat_to_R(pose[3:]) @ PC.T).T + pose[:3]

In [20]:
fig = go.Figure(data=pc_plot_trace(PC))
fig.update_layout(width=1500, height=900, scene=dict(aspectmode='data'))
fig.show()

In [21]:
# Clean up point cloud
# Remove points below ground plane
PC = PC[PC[:,2] > -0.1]

# Remove points outside of x/y room bounds
X_BOUNDS = [-5, 5]
Y_BOUNDS = [-3, 3]
PC = PC[np.bitwise_and(PC[:,0] > X_BOUNDS[0], PC[:,0] < X_BOUNDS[1])]
PC = PC[np.bitwise_and(PC[:,1] > Y_BOUNDS[0], PC[:,1] < Y_BOUNDS[1])]

# Transform back
PC = PC - pose[:3]

# Downsample 
PC = adaptive_downsample(PC, factor=5)
#PC = downsample(PC, factor=5, axis=0)

In [22]:
fig = go.Figure(data=pc_plot_trace(PC))
fig.update_layout(width=1500, height=900, scene=dict(aspectmode='data'))
fig.show()

In [23]:
# Create the mesh
mesh = LidarMesh(PC)
mesh.prune(edge_len_lim=0.5)
start_time = time.time()
# Cluster the mesh with graph search
clusters, avg_normals = cluster_mesh_graph_search(mesh)
print("elapsed time: ", time.time() - start_time)

elapsed time:  0.018004417419433594


In [31]:
import open3d as o3d

o3d_mesh = o3d.geometry.TriangleMesh()
o3d_mesh.vertices = o3d.utility.Vector3dVector(mesh.P)
o3d_mesh.triangles = o3d.utility.Vector3iVector(mesh.DT.simplices)

o3d.visualization.draw_geometries([o3d_mesh])

In [46]:
smoothed_mesh = o3d_mesh.filter_smooth_laplacian(number_of_iterations=5)

In [47]:
np.asarray(smoothed_mesh.vertices)

array([[        nan,         nan,         nan],
       [ 1.00310468, -0.71156544, -0.19296996],
       [ 0.29749723, -0.64827729,  0.03864429],
       ...,
       [-1.57886852, -0.30141776,  0.27552214],
       [ 0.28042095, -0.63426025,  0.08905383],
       [-1.58968582, -0.28400693,  0.09300234]])

In [48]:
mesh.P = np.asarray(smoothed_mesh.vertices)

In [49]:
mesh.P

array([[        nan,         nan,         nan],
       [ 1.00310468, -0.71156544, -0.19296996],
       [ 0.29749723, -0.64827729,  0.03864429],
       ...,
       [-1.57886852, -0.30141776,  0.27552214],
       [ 0.28042095, -0.63426025,  0.08905383],
       [-1.58968582, -0.28400693,  0.09300234]])

In [50]:
# Plot mesh
fig = go.Figure(data=mesh.plot_trace())
fig.update_layout(width=1500, height=900, scene=dict(aspectmode='data'))
fig.show()

In [51]:
clusters, avg_normals = cluster_mesh_graph_search(mesh)

In [52]:
# Plot clusters
plot_clusters(PC, mesh, clusters)

In [106]:
planes = planes_from_clusters(mesh, clusters, avg_normals)
scan = Scan(planes)

basis z normal  [5.09549460e-04 1.71518539e-03 9.99998399e-01]


In [107]:
fig = go.Figure(data=[pc_plot_trace(PC)]+scan.plot_trace())
fig.update_layout(width=1500, height=900, scene=dict(aspectmode='data'))
fig.show()

In [84]:
for 

array([[-1.51354623e-16]])

In [87]:
np.dot(avg_normals[0], avg_normals[2])

-0.05411727553943005

In [104]:
from planeslam.general import normalize

v = avg_normals[0]
n = avg_normals[2][:,None]

v_proj = normalize(v - (v @ n) @ n.T)

In [105]:
np.dot(v_proj, n)

array([4.11996826e-18])

In [91]:
from planeslam.geometry.util import project_points_to_plane

n_proj = project_points_to_plane(avg_normals[0], avg_normals[2][:,None])
np.dot(n_proj, avg_normals[2])

0.3106866725889578

In [93]:
n_proj

array([-0.01236008,  0.99898754,  0.30898002])

In [92]:
avg_normals[2][:,None]

array([[5.09549460e-04],
       [1.71518539e-03],
       [9.99998399e-01]])

In [80]:
for p in scan.planes:
    print(p.normal)

[[-0.01253676]
 [ 0.99991995]
 [-0.00170866]]
[[ 0.01253676]
 [-0.99991995]
 [ 0.00170866]]
[[-1.69652707e-04]
 [ 5.58256155e-02]
 [ 9.98440520e-01]]
[[-1.69652707e-04]
 [ 5.58256155e-02]
 [ 9.98440520e-01]]
[[-1.69652707e-04]
 [ 5.58256155e-02]
 [ 9.98440520e-01]]
[[-9.98455984e-01]
 [-1.25175022e-02]
 [ 5.30233393e-04]]
[[ 0.01253676]
 [-0.99991995]
 [ 0.00170866]]
[[ 9.98455984e-01]
 [ 1.25175022e-02]
 [-5.30233393e-04]]
[[-1.69652707e-04]
 [ 5.58256155e-02]
 [ 9.98440520e-01]]
[[-9.98455984e-01]
 [-1.25175022e-02]
 [ 5.30233393e-04]]
[[ 9.98455984e-01]
 [ 1.25175022e-02]
 [-5.30233393e-04]]
[[ 0.01253676]
 [-0.99991995]
 [ 0.00170866]]
[[ 9.98455984e-01]
 [ 1.25175022e-02]
 [-5.30233393e-04]]
[[-0.01253676]
 [ 0.99991995]
 [-0.00170866]]
[[ 0.01253676]
 [-0.99991995]
 [ 0.00170866]]
[[-0.01253676]
 [ 0.99991995]
 [-0.00170866]]
[[ 0.01253676]
 [-0.99991995]
 [ 0.00170866]]
[[ 0.01253676]
 [-0.99991995]
 [ 0.00170866]]
[[ 0.01253676]
 [-0.99991995]
 [ 0.00170866]]
[[-1.69652707e-04]

In [70]:
normals_arr[np.argmax(np.abs(normals_arr), axis=1)==2][0]

array([5.09549460e-04, 1.71518539e-03, 9.99998399e-01])

In [ ]:
from planeslam.scan import velo_pc_to_scan
scan = velo_pc_to_scan(PC, ds_rate=5, edge_len_lim=2)

In [ ]:
fig = go.Figure(data=scan.plot_trace())
fig.update_layout(width=1000, height=600, scene=dict(aspectmode='data'))
fig.show()

In [140]:
from planeslam.clustering import mesh_cluster_pts, sort_mesh_clusters

clusters, avg_normals = sort_mesh_clusters(clusters, avg_normals)
i = 0
n = avg_normals[i][:,None]
c = clusters[i]
cluster_pts = mesh_cluster_pts(mesh, c)  # Extract points from cluster

In [141]:
n

array([[-0.01006203],
       [-0.00650675],
       [ 0.99992821]])

In [83]:
# Plot the points 
fig = go.Figure(data=pc_plot_trace(cluster_pts))
fig.update_layout(width=1000, height=600, scene=dict(aspectmode='data'))
fig.show()

In [73]:
# Find extraction basis based on normals
basis = np.zeros((3,3))
basis[:,2] = avg_normals[0]  # choose first cluster's normal as z
dps = np.asarray(avg_normals) @ basis[:,2]
orth_idxs = np.nonzero(np.abs(dps) < 0.2)[0]  # indices of normals approximately orthonormal to z
basis[:,0] = avg_normals[orth_idxs[0]]  # choose the first one as x
basis[:,1] = np.cross(basis[:,2], basis[:,0])

In [74]:
basis

array([[ 5.09549460e-04,  9.98455984e-01, -1.25459671e-02],
       [ 1.71518539e-03,  1.25175022e-02,  9.98361834e-01],
       [ 9.99998399e-01, -5.30233393e-04, -5.58233477e-02]])

In [76]:
basis.T @ basis

array([[ 1.00000000e+00,  2.38671390e-20, -5.41172755e-02],
       [ 2.38671390e-20,  9.97071320e-01, -8.61922792e-20],
       [-5.41172755e-02, -8.61922792e-20,  1.00000000e+00]])